In [1]:
import math
import numpy as np
from scipy.integrate import ode
import plotly.graph_objects as go

In [2]:
# Planet Initializers
def spheres(size, clr, clr_gradient=None, dist=0): 
    
    # Set up 100 points. First, do angles
    theta = np.linspace(0,2*np.pi,100)
    phi = np.linspace(0,np.pi,100)
    
    # Set up coordinates for points on the sphere
    x0 = dist + size * np.outer(np.cos(theta),np.sin(phi))
    y0 = size * np.outer(np.sin(theta),np.sin(phi))
    z0 = size * np.outer(np.ones(100),np.cos(phi))
    
    # Set up trace
    if clr_gradient == None:
        clr_gradient = clr
    else:
        pass
    
    trace = go.Surface(x=x0, y=y0, z=z0, colorscale=[[0, clr], [1, clr_gradient]])
    trace.update(showscale=False)

    return trace

# Orbit Initializer
class Orbits:
    def diffy_q(t, y, mu):
        # Unpack State R-Position Vector V-Velocity Vector, Inputs(Position & Velocity)
        rx, ry, rz, vx, vy, vz = y
        r = np.array([rx, ry, rz])

        # Norm of Radius Vector
        norm_r = np.linalg.norm(r)

        # Two Body Acceleration
        ax, ay, az = -r * Earth_mu/norm_r**3

        # Outputs-The Derivatives of Input, Outputs(Velocity, Acceleration)
        return [vx, vy, vz, ax, ay, az]  
    

In [10]:
planet_radii = {'Earth': 6378.0}
Earth = spheres(planet_radii['Earth'], 'dodgerblue', 'mediumseagreen')

print(planet_radii['Earth'])

layout=go.Layout(title = 'Solar System', showlegend=False, margin=dict(l=0, r=0, t=0, b=0),
                  #paper_bgcolor = 'black',
                  scene = dict(xaxis=dict(title='x (km)'),
                               yaxis=dict(title='y (km)'),
                               zaxis=dict(title='z (km)')
                               ))

fig = go.Figure(data = [Earth], layout = layout)

fig.show()

fig.write_html("Solar_system.html")

6378.0


In [11]:
Earth_mu = 398600.0

# Initial Conditions of Orbital Parameters
h = 500 # km - Spacecraft's Distance from the center of Earth
r_mag = planet_radii['Earth'] + h # Magnitude of Position Vector (Earth's Radius + Spacecraft's Height)
v_mag = np.sqrt(Earth_mu / r_mag) # Magniitude of Velocity Vector (Tangential Velocity / Speed of a Satellite in Circular Orbit)

print(r_mag)

r_vec = [r_mag, 0, 0] # Position Vector ((r_mag)i + (0)j + (0)k)
v_vec = [0, v_mag, 0] # Velocity Vector ((0)i + (v_mag)j + (0)k

timespan = 100*60.0 # Timespan
dt = 100 # Timestep

n_steps = int(np.ceil(timespan/dt)) # Total number of steps

# Initializing arrays - Preallocating Memory 
ys = np.zeros((n_steps, 6))
ts = np.zeros((n_steps, 1))

# Initial Conditions
y0 = r_vec + v_vec
ys[0] = np.array(y0)
step = 1

# Initializing Solver
solver = ode(Orbits.diffy_q)
solver.set_integrator('lsoda')
solver.set_initial_value(y0, 0)
solver.set_f_params(Earth_mu)


# Propagate Orbit
while solver.successful() and step < n_steps:
    solver.integrate(solver.t + dt)
    ts[step] = solver.t
    ys[step] = solver.y
    step += 1

    rs = ys[:, :3]
    vs = ys[:, 3:]

# String Parsing 
rxs = []
rys = []
rzs = []
for r in rs:
    rxs.append(r[0])
    rys.append(r[1])
    rzs.append(r[2])
    
rs_trace = go.Scatter3d(x=rxs, y=rys, z=rzs, marker=dict(size=0.1), line=dict(color="black",width=2), name="Trajectory")
rs_starting = go.Scatter3d(x=[rxs[0]], y=[rys[0]], z=[rzs[0]], marker=dict(color='black',size=4), name="Initial Position"
)

layout=go.Layout(title = 'Solar System', showlegend=True, margin=dict(l=0, r=0, t=0, b=0),
                  #paper_bgcolor = 'black',
                  scene = dict(xaxis=dict(title='x (km)'),
                               yaxis=dict(title='y (km)'),
                               zaxis=dict(title='z (km)')
                               ))

fig = go.Figure(data = [Earth, rs_trace, rs_starting], layout = layout)

fig.show()
print(rs_trace)
fig.write_html("Solar_system.html")

6878.0


Scatter3d({
    'line': {'color': 'black', 'width': 2},
    'marker': {'size': 0.1},
    'name': 'Trajectory',
    'x': [6878.0, 6835.914839288539, 6710.177380254426, 6502.312441869967,
          6214.8763994951405, 5851.382502794787, 5416.27900678513,
          4914.891327420441, 4353.357454075871, 3738.548516979207,
          3077.986840562618, 2379.7567754220486, 1652.404000952508,
          904.8295390119082, 146.18167424281245, -614.2549552537896,
          -1367.1742418246324, -2103.362288037286, -2813.809725196983,
          -3489.821993973302, -4123.126002855225, -4705.971466472668,
          -5231.225672528279, -5692.4606980166745, -6084.032045282283,
          -6401.147709744463, -6639.926830226154, -6797.447200993091,
          -6871.781046561186, -6862.0213104984105, -6768.287543733845,
          -6591.717957927301, -6334.4816062387945, -5999.723397368163,
          -5591.5396988334205, -5114.926182082776, -4575.717530120077,
          -3980.5116001340866, -3336.59109948703

In [12]:
# Initial Conditions of Orbital Parameters
h = 1000 # km - Spacecraft's Distance from the center of Earth
r_mag = planet_radii['Earth'] + planet_radii['Earth'] * 4 # Magnitude of Position Vector (Earth's Radius + Spacecraft's Height)
v_mag = np.sqrt(Earth_mu / r_mag) # Magniitude of Velocity Vector (Tangential Velocity / Speed of a Satellite in Circular Orbit)

print(r_mag)

r_vec = [r_mag, r_mag*0.01, r_mag*-0.05] # Position Vector ((r_mag)i + (0)j + (0)k)
v_vec = [0, v_mag, v_mag*0.8] # Velocity Vector ((0)i + (v_mag)j + (0)k

timespan = 3600*24.0 # Timespan
dt = 100 # Timestep

n_steps = int(np.ceil(timespan/dt)) # Total number of steps

# Initializing arrays - Preallocating Memory 
ys = np.zeros((n_steps, 6))
ts = np.zeros((n_steps, 1))

# Initial Conditions
y0 = r_vec + v_vec
ys[0] = np.array(y0)
step = 1

# Initializing Solver
solver = ode(Orbits.diffy_q)
solver.set_integrator('lsoda')
solver.set_initial_value(y0, 0)
solver.set_f_params(Earth_mu)


# Propagate Orbit
while solver.successful() and step < n_steps:
    solver.integrate(solver.t + dt)
    ts[step] = solver.t
    ys[step] = solver.y
    step += 1

    rs = ys[:, :3]
    vs = ys[:, 3:]

# String Parsing 
rxs = []
rys = []
rzs = []
for r in rs:
    rxs.append(r[0])
    rys.append(r[1])
    rzs.append(r[2])
    
rs_trace = go.Scatter3d(x=rxs, y=rys, z=rzs, marker=dict(size=0.1), line=dict(color="black",width=2), name="Trajectory")
rs_starting = go.Scatter3d(x=[rxs[0]], y=[rys[0]], z=[rzs[0]], marker=dict(color='black',size=4), name="Initial Position"
)

layout=go.Layout(title = 'Solar System', showlegend=True, margin=dict(l=0, r=0, t=0, b=0),
                  #paper_bgcolor = 'black',
                  scene = dict(xaxis=dict(title='x (km)'),
                               yaxis=dict(title='y (km)'),
                               zaxis=dict(title='z (km)')
                               ))

fig = go.Figure(data = [Earth, rs_trace, rs_starting], layout = layout)


fig.show()
print(rs_trace)
fig.write_html("Solar_system.html")

31890.0


Scatter3d({
    'line': {'color': 'black', 'width': 2},
    'marker': {'size': 0.1},
    'name': 'Trajectory',
    'x': [31890.0, 31888.047289603706, 31882.187265771652, ...,
          -127019.02417151723, -127106.88099882449, -127194.52328660298],
    'y': [318.90000000000003, 672.4155594363235, 1025.8487217172797, ...,
          27161.021569634708, 27091.04632721784, 27021.02535838641],
    'z': [-1594.5, -1311.5742952479573, -1028.487884040932, ...,
          29095.92065765566, 29045.036159705985, 28994.102637332]
})


In [13]:
# Initial Conditions of Orbital Parameters
h = 1000 # km - Spacecraft's Distance from the center of Earth
r_mag = planet_radii['Earth'] + 1500.0 # Magnitude of Position Vector (Earth's Radius + Spacecraft's Height)
v_mag = np.sqrt(Earth_mu / r_mag) # Magniitude of Velocity Vector (Tangential Velocity / Speed of a Satellite in Circular Orbit)

print(r_mag)

r_vec = [r_mag, r_mag*0.01, r_mag*-0.01] # Position Vector ((r_mag)i + (0)j + (0)k)
v_vec = [0, v_mag, v_mag*0.3] # Velocity Vector ((0)i + (v_mag)j + (0)k

timespan = 3600*24.0 # Timespan
dt = 100 # Timestep

n_steps = int(np.ceil(timespan/dt)) # Total number of steps

# Initializing arrays - Preallocating Memory 
ys = np.zeros((n_steps, 6))
ts = np.zeros((n_steps, 1))

# Initial Conditions
y0 = r_vec + v_vec
ys[0] = np.array(y0)
step = 1

# Initializing Solver
solver = ode(Orbits.diffy_q)
solver.set_integrator('lsoda')
solver.set_initial_value(y0, 0)
solver.set_f_params(Earth_mu)


# Propagate Orbit
while solver.successful() and step < n_steps:
    solver.integrate(solver.t + dt)
    ts[step] = solver.t
    ys[step] = solver.y
    step += 1

    rs = ys[:, :3]
    vs = ys[:, 3:]

# String Parsing 
rxs = []
rys = []
rzs = []
for r in rs:
    rxs.append(r[0])
    rys.append(r[1])
    rzs.append(r[2])
    
rs_trace = go.Scatter3d(x=rxs, y=rys, z=rzs, marker=dict(size=0.1), line=dict(color="black",width=2), name="Trajectory")
rs_starting = go.Scatter3d(x=[rxs[0]], y=[rys[0]], z=[rzs[0]], marker=dict(color='black',size=4), name="Initial Position"
)

layout=go.Layout(title = 'Solar System', showlegend=True, margin=dict(l=0, r=0, t=0, b=0),
                  #paper_bgcolor = 'black',
                  scene = dict(xaxis=dict(title='x (km)'),
                               yaxis=dict(title='y (km)'),
                               zaxis=dict(title='z (km)')
                               ))

fig = go.Figure(data = [Earth, rs_trace, rs_starting], layout = layout)


fig.show()
print(rs_trace)
fig.write_html("Solar_system.html")

7878.0


Scatter3d({
    'line': {'color': 'black', 'width': 2},
    'marker': {'size': 0.1},
    'name': 'Trajectory',
    'x': [7878.0, 7845.945011842065, 7750.19218823242, ..., -2329.1848129157124,
          -1661.7229681933206, -984.1568447181605],
    'y': [78.78, 788.8077418924563, 1492.4357676190152, ..., -8079.020877305222,
          -8167.3852852822365, -8206.012024304166],
    'z': [-78.78, 134.64503741378996, 346.97823183868303, ..., -2393.426860623674,
          -2428.6131869981705, -2449.0095683099266]
})


In [14]:
# Initial Conditions of Orbital Parameters
h = 1000 # km - Spacecraft's Distance from the center of Earth
r_mag = planet_radii['Earth'] + 14500.0 # Magnitude of Position Vector (Earth's Radius + Spacecraft's Height)
v_mag = np.sqrt(Earth_mu / r_mag) # Magniitude of Velocity Vector (Tangential Velocity / Speed of a Satellite in Circular Orbit)

print(r_mag)

r_vec = [r_mag, r_mag*0.01, r_mag*-0.05] # Position Vector ((r_mag)i + (0)j + (0)k)
v_vec = [0, v_mag, v_mag*0.8] # Velocity Vector ((0)i + (v_mag)j + (0)k

timespan = 6*3600*24.0 # Timespan
dt = 100 # Timestep

n_steps = int(np.ceil(timespan/dt)) # Total number of steps

# Initializing arrays - Preallocating Memory 
ys = np.zeros((n_steps, 6))
ts = np.zeros((n_steps, 1))

# Initial Conditions
y0 = r_vec + v_vec
ys[0] = np.array(y0)
step = 1

# Initializing Solver
solver = ode(Orbits.diffy_q)
solver.set_integrator('lsoda')
solver.set_initial_value(y0, 0)
solver.set_f_params(Earth_mu)


# Propagate Orbit
while solver.successful() and step < n_steps:
    solver.integrate(solver.t + dt)
    ts[step] = solver.t
    ys[step] = solver.y
    step += 1

    rs = ys[:, :3]
    vs = ys[:, 3:]

# String Parsing 
rxs = []
rys = []
rzs = []
for r in rs:
    rxs.append(r[0])
    rys.append(r[1])
    rzs.append(r[2])
    
rs_trace = go.Scatter3d(x=rxs, y=rys, z=rzs, marker=dict(size=0.1), line=dict(color="black",width=2), name="Trajectory")
rs_starting = go.Scatter3d(x=[rxs[0]], y=[rys[0]], z=[rzs[0]], marker=dict(color='black',size=4), name="Initial Position"
)

layout=go.Layout(title = 'Solar System', showlegend=True, margin=dict(l=0, r=0, t=0, b=0),
                  #paper_bgcolor = 'black',
                  scene = dict(xaxis=dict(title='x (km)'),
                               yaxis=dict(title='y (km)'),
                               zaxis=dict(title='z (km)')
                               ))

fig = go.Figure(data = [Earth, rs_trace, rs_starting], layout = layout)


fig.show()
print(rs_trace)
fig.write_html("Solar_system.html")

20878.0


Scatter3d({
    'line': {'color': 'black', 'width': 2},
    'marker': {'size': 0.1},
    'name': 'Trajectory',
    'x': [20878.0, 20873.4431598641, 20859.7670392023, ..., -79597.33563233427,
          -79474.85146658916, -79351.87195537834],
    'y': [208.78, 645.6450452077455, 1082.2279862300634, ..., -28000.896431632766,
          -28072.41500736087, -28143.758609058856],
    'z': [-1043.9, -694.143667105916, -344.0840992896519, ...,
          -17784.071678643537, -17848.390620839218, -17912.598313847815]
})
